In [46]:
import yfinance as yf
import pandas as pd
import numpy as np
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import TimeSeriesSplit
import os

# 股票列表
tickers = ['AAPL', 'MSFT', 'GOOGL', 'AMZN', 'TSLA',]  # 科技
tickers += ['JPM', 'BAC', 'C', 'WFC', 'GS',]            # 金融
tickers += ['JNJ', 'PFE', 'MRK', 'ABBV', 'BMY',]         # 医药
tickers += ['XOM', 'CVX', 'COP', 'SLB', 'BKR',]          # 能源
tickers += ['DIS', 'NFLX', 'CMCSA', 'NKE', 'SBUX',]      # 消费
tickers += ['CAT', 'DE', 'MMM', 'GE', 'HON']            # 工业


num_features_to_keep = 9
start_date = '2020-01-01'
end_date = '2022-01-01'


In [47]:
def get_stock_data(ticker):
    data = yf.download(ticker, start=start_date, end=end_date)
    data['Year'] = data.index.year
    data['Month'] = data.index.month
    data['Day'] = data.index.day

    close = data['Close'].shift(1)

    data['MA5'] = close.rolling(window=5).mean()
    data['MA10'] = close.rolling(window=10).mean()
    data['MA20'] = close.rolling(window=20).mean()

    delta = close.diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    RS = gain / loss
    RSI = 100 - (100 / (1 + RS))
    data.loc[data.index >= RSI.index[0], 'RSI'] = RSI

    exp1 = close.ewm(span=12, adjust=False).mean()
    exp2 = close.ewm(span=26, adjust=False).mean()
    MACD = exp1 - exp2
    data.loc[data.index >= MACD.index[0], 'MACD'] = MACD

    data['VWAP'] = (close * data['Volume']).cumsum() / data['Volume'].cumsum()

    period = 20
    data['SMA'] = close.rolling(window=period).mean()
    data['Std_dev'] = close.rolling(window=period).std()
    data['Upper_band'] = data['SMA'] + 2 * data['Std_dev']
    data['Lower_band'] = data['SMA'] - 2 * data['Std_dev']

    benchmark_data = yf.download('SPY', start=start_date, end=end_date)['Close']
    data['Relative_Performance'] = (close / benchmark_data.values) * 100

    data['ROC'] = (close.pct_change(periods=1)) * 100

    high_low_range = data['High'] - data['Low']
    high_close_range = abs(data['High'].shift(1) - close.shift(1))
    low_close_range = abs(data['Low'].shift(1) - close.shift(1))
    true_range = pd.concat([high_low_range, high_close_range, low_close_range], axis=1).max(axis=1)
    data['ATR'] = true_range.rolling(window=14).mean()

    data['Close_yes'] = data['Close'].shift(1)
    data['Open_yes'] = data['Open'].shift(1)
    data['High_yes'] = data['High'].shift(1)
    data['Low_yes'] = data['Low'].shift(1)

    data = data.dropna()
    return data

# 获取所有股票数据
stock_data = {ticker: get_stock_data(ticker) for ticker in tickers}
for ticker, data in stock_data.items():
    print(f"{ticker} data:\n{data.head()}\n")

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

AAPL data:
                 Open       High        Low      Close  Adj Close     Volume  \
Date                                                                           
2020-01-31  80.232498  80.669998  77.072502  77.377502  75.086937  199588384   
2020-02-03  76.074997  78.372498  75.555000  77.165001  74.880722  173985604   
2020-02-04  78.827499  79.910004  78.408623  79.712502  77.352806  136616536   
2020-02-05  80.879997  81.190002  79.737503  80.362503  77.983574  118826872   
2020-02-06  80.642502  81.305000  80.066200  81.302498  78.895744  105425540   

            Year  Month  Day        MA5  ...   Std_dev  Upper_band  \
Date                                     ...                         
2020-01-31  2020      1   31  79.658000  ...  2.091398   82.191922   
2020-02-03  2020      2    3  79.218001  ...  1.982899   82.089422   
2020-02-04  2020      2    4  79.203500  ...  1.792484   81.848969   
2020-02-05  2020      2    5  79.261501  ...  1.638813   81.779752   
2020-02-

In [48]:
def format_feature(data):
    features = ['Volume', 'Year', 'Month', 'Day', 'MA5', 'MA10', 'MA20', 'RSI', 'MACD', 
                'VWAP', 'SMA', 'Std_dev', 'Upper_band', 'Lower_band', 'Relative_Performance', 'ATR',
                'Close_yes', 'Open_yes', 'High_yes', 'Low_yes']
    X = data[features]
    y = data['Close'].pct_change()
    X = X.iloc[1:]
    y = y.iloc[1:]
    return X, y

# 格式化数据
stock_features = {ticker: format_feature(data) for ticker, data in stock_data.items()}
for ticker, (X, y) in stock_features.items():
    print(f"{ticker} features:\nX:\n{X.head()}\ny:\n{y.head()}\n")

AAPL features:
X:
               Volume  Year  Month  Day        MA5       MA10       MA20  \
Date                                                                       
2020-02-03  173985604  2020      2    3  79.218001  79.372501  78.123625   
2020-02-04  136616536  2020      2    4  79.203500  79.120751  78.264000   
2020-02-05  118826872  2020      2    5  79.261501  79.177751  78.502126   
2020-02-06  105425540  2020      2    6  79.117001  79.271501  78.790376   
2020-02-07  117684048  2020      2    7  79.184001  79.421001  79.065625   

                  RSI      MACD       VWAP        SMA   Std_dev  Upper_band  \
Date                                                                          
2020-02-03  49.368860  1.002945  74.662187  78.123625  1.982899   82.089422   
2020-02-04  42.987505  0.789509  74.767591  78.264000  1.792484   81.848969   
2020-02-05  54.739602  0.816509  74.942322  78.502126  1.638813   81.779752   
2020-02-06  57.618700  0.880210  75.107082  78.790376 

In [49]:
def format_feature(data):
    features = ['Volume', 'Year', 'Month', 'Day', 'MA5', 'MA10', 'MA20', 'RSI', 'MACD', 
                'VWAP', 'SMA', 'Std_dev', 'Upper_band', 'Lower_band', 'Relative_Performance', 'ATR',
                'Close_yes', 'Open_yes', 'High_yes', 'Low_yes']
    X = data[features]
    y = data['Close'].pct_change()
    X = X.iloc[1:]
    y = y.iloc[1:]
    return X, y

# 格式化数据
stock_features = {ticker: format_feature(data) for ticker, data in stock_data.items()}
for ticker, (X, y) in stock_features.items():
    print(f"{ticker} features:\nX:\n{X.head()}\ny:\n{y.head()}\n")


AAPL features:
X:
               Volume  Year  Month  Day        MA5       MA10       MA20  \
Date                                                                       
2020-02-03  173985604  2020      2    3  79.218001  79.372501  78.123625   
2020-02-04  136616536  2020      2    4  79.203500  79.120751  78.264000   
2020-02-05  118826872  2020      2    5  79.261501  79.177751  78.502126   
2020-02-06  105425540  2020      2    6  79.117001  79.271501  78.790376   
2020-02-07  117684048  2020      2    7  79.184001  79.421001  79.065625   

                  RSI      MACD       VWAP        SMA   Std_dev  Upper_band  \
Date                                                                          
2020-02-03  49.368860  1.002945  74.662187  78.123625  1.982899   82.089422   
2020-02-04  42.987505  0.789509  74.767591  78.264000  1.792484   81.848969   
2020-02-05  54.739602  0.816509  74.942322  78.502126  1.638813   81.779752   
2020-02-06  57.618700  0.880210  75.107082  78.790376 

In [50]:
import lightgbm as lgb

def feature_selection_for_stocks(stock_features, best_params, num_features_to_keep=8):
    feature_importances_all = {}
    stock_features_selected = {}

    # 训练模型，获得所有股票的特征重要度
    for ticker, (X, y) in stock_features.items():
        params = best_params

        lgb_model = lgb.LGBMRegressor(objective='regression', random_state=42, **params)
        lgb_model.fit(X, y)
        feature_importances = lgb_model.feature_importances_

        feature_importance_list = [(feature, importance) for feature, importance in zip(X.columns, feature_importances)]
        feature_importance_list.sort(key=lambda x: x[1], reverse=True)

        feature_importances_all[ticker] = feature_importance_list

    # 打印每支股票的特征重要度排名
    for ticker, importance_list in feature_importances_all.items():
        for feature, importance in importance_list:
            pass
    feature_importance_totals = {}
    # 平均值
    for stock, feature_importances in feature_importances_all.items():
        for feature, importance in feature_importances:
            if feature in feature_importance_totals:
                feature_importance_totals[feature] += importance
            else:
                feature_importance_totals[feature] = importance
    num_stocks = len(feature_importances_all)
    average_feature_importances = {feature: importance / num_stocks for feature, importance in
                                   feature_importance_totals.items()}
    for feature, avg_importance in average_feature_importances.items():
        print(f"Average importance of {feature} across all stocks: {avg_importance:.2f}")

    # 只保留重要的特征
    importance_list = sorted(average_feature_importances.items(), key=lambda x: x[1], reverse=True)
    importance_list = importance_list[:num_features_to_keep]
    important_features = [feature for feature, importance in importance_list[:num_features_to_keep]]
    print(f"Selected the top{num_features_to_keep} stocks: {important_features}")
    for stock in stock_features:
        stock_features_selected[stock] = stock_features[stock]
    return stock_features_selected

# 进行特征选择
temp_params = {'colsample_bytree': 0.7, 'learning_rate': 0.01, 'max_depth': 12, 'n_estimators': 100, 'subsample': 0.8}
stock_features_selected = feature_selection_for_stocks(stock_features, temp_params, num_features_to_keep=8)


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000217 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2801
[LightGBM] [Info] Number of data points in the train set: 484, number of used features: 20
[LightGBM] [Info] Start training from score 0.002001
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

In [51]:
stock_features_selected

{'AAPL': (               Volume  Year  Month  Day         MA5        MA10        MA20  \
  Date                                                                          
  2020-02-03  173985604  2020      2    3   79.218001   79.372501   78.123625   
  2020-02-04  136616536  2020      2    4   79.203500   79.120751   78.264000   
  2020-02-05  118826872  2020      2    5   79.261501   79.177751   78.502126   
  2020-02-06  105425540  2020      2    6   79.117001   79.271501   78.790376   
  2020-02-07  117684048  2020      2    7   79.184001   79.421001   79.065625   
  ...               ...   ...    ...  ...         ...         ...         ...   
  2021-12-27   74919582  2021     12   27  173.160001  174.688000  170.287000   
  2021-12-28   79144339  2021     12   28  174.998001  174.776001  171.463000   
  2021-12-29   62348931  2021     12   29  176.906000  175.131000  172.415500   
  2021-12-30   59773014  2021     12   30  178.184000  175.636000  173.119500   
  2021-12-31   64062

In [90]:
import lightgbm as lgb
import pandas as pd
import numpy as np
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import os
import pickle

# 定义全局参数
future_days = 1  # 预测未来一天的交易日数

def train_and_predict_lightgbm(ticker, X, y, params=None):
    if params is None:
        params = {
            'objective': 'regression',
            'metric': 'rmse',
            'boosting_type': 'gbdt',
            'learning_rate': 0.05,
            'num_leaves': 31,
            'feature_fraction': 0.9,
            'bagging_fraction': 0.8,
            'bagging_freq': 5,
            'verbose': 0
        }

    # Split data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Create LightGBM dataset
    train_data = lgb.Dataset(X_train, label=y_train)
    test_data = lgb.Dataset(X_test, label=y_test, reference=train_data)

    # Define early stopping callback
    callbacks = [lgb.early_stopping(stopping_rounds=10)]

    # Train model
    model = lgb.train(params, train_data, valid_sets=[test_data], callbacks=callbacks)

    # Predict on the test set
    y_pred = model.predict(X_test, num_iteration=model.best_iteration)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    print(f'RMSE for {ticker}: {rmse}')

    # Predict future trends
    future_predictions = []
    last_data = X.iloc[-future_days:].copy()
    for _ in range(future_days):
        pred = model.predict(last_data.values[-1].reshape(1, -1), num_iteration=model.best_iteration)[0]
        future_predictions.append(pred)
        new_row = last_data.iloc[-1].copy()
        new_row['Close'] = pred  # Assume 'Close' is one of the features
        last_data = pd.concat([last_data, pd.DataFrame([new_row])], ignore_index=True)
        last_data = last_data.iloc[1:]

    return model, X_test, y_test, y_pred, future_predictions

def evaluate_model(ticker, X_test, y_test, y_pred, future_predictions):
    test_indices = X_test.index
    actual_percentages = y_test.values * 100
    predict_percentages = y_pred * 100

    future_dates = pd.date_range(start=test_indices[-1], periods=len(future_predictions) + 1, inclusive='right')
    future_percentages = np.array(future_predictions) * 100

    delta = [p - a for p, a in zip(predict_percentages, actual_percentages)]
    result = pd.DataFrame({
        'predict_percentages(%)': predict_percentages,
        'actual_percentages(%)': actual_percentages,
        'delta(%)': delta
    })
    print(result)

    # 简单策略的收益率
    print("Naive strategy earn rate:", sum(actual_percentages), "%")

    # LightGBM策略的收益率
    lightgbm_strategy_earn = []
    for i, predict in enumerate(predict_percentages):
        if predict > 0:
            lightgbm_strategy_earn.append(actual_percentages[i])
        else:
            lightgbm_strategy_earn.append(0)
    print("LightGBM strategy earn rate:", sum(lightgbm_strategy_earn), "%")

    acc = 0
    for pred1, pred2 in zip(predict_percentages, actual_percentages):
        print("pred:", pred1, "actu:", pred2)
        if pred1 * pred2 > 0:
            acc += 1
    acc /= len(predict_percentages)
    print("acc:", acc)

    # 绘制累积收益率曲线
    cumulative_naive_percentage = np.cumsum(actual_percentages)
    cumulative_lightgbm_percentage = np.cumsum(lightgbm_strategy_earn)
    plt.figure(figsize=(10, 6))
    plt.plot(test_indices, cumulative_naive_percentage, marker='o', markersize=3, linestyle='-', color='blue',
             label='Naive Strategy')
    plt.plot(test_indices, cumulative_lightgbm_percentage, marker='o', markersize=3, linestyle='-', color='orange',
             label='LightGBM Strategy')

    # 绘制未来收益率曲线
    future_cumulative_percentage = np.cumsum(future_percentages)
    future_dates_full = pd.concat([pd.Series(test_indices[-1]), pd.Series(future_dates)])
    future_cumulative_full = pd.concat([pd.Series(cumulative_lightgbm_percentage[-1]), pd.Series(future_cumulative_percentage)])
    plt.plot(future_dates_full, future_cumulative_full, marker='o', markersize=3, linestyle='-', color='green',
             label='Future Prediction')

    plt.title(f'Daily Earnings Percentages for {ticker}')
    plt.xlabel('Date')
    plt.ylabel('Percentage (%)')
    plt.xticks(rotation=45)
    plt.grid(True)
    plt.legend()
    plt.tight_layout()

    if not os.path.exists('pic/lightGBM'):
        os.makedirs('pic/lightGBM')
    plt.savefig(f'pic/lightGBM/{ticker}.png')
    plt.close()

    predict_result = {str(date): pred / 100 for date, pred in zip(test_indices, predict_percentages)}
    return predict_result, future_predictions
# 确保目录存在
if not os.path.exists('predictions/LightGBM'):
    os.makedirs('predictions/LightGBM')

# 对所有的tickers进行预测和评估
all_predictions_lightgbm = {}
for ticker in tickers:
    X, y = stock_features_selected[ticker]
    model, X_test, y_test, y_pred, future_predictions = train_and_predict_lightgbm(ticker, X, y)
    predict_result, future_result = evaluate_model(ticker, X_test, y_test, y_pred, future_predictions)
    all_predictions_lightgbm[ticker] = future_result

    # 保存预测结果
    file_path = os.path.join('predictions/LightGBM', f'{ticker}_predictions.pkl')
    with open(file_path, 'wb') as file:
        pickle.dump(future_result, file)
        print(f'Saved predictions for {ticker} to {file_path}')

print("All predictions have been saved.")


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

In [ ]:
import lightgbm as lgb
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import mean_squared_error
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
# 定义用于归一化的 MinMaxScaler 实例
scaler_y = MinMaxScaler()
scaler_X = MinMaxScaler()

def prepare_data(data, n_steps):
    X, y = [], []
    for i in range(len(data) - n_steps):
        X.append(data[i:i + n_steps])  # 输入序列
        y.append(data[i + n_steps])    # 目标值
    return np.array(X), np.array(y)

def get_stock_data(ticker):
    data = yf.download(ticker, start=start_date, end=end_date)
    data['Year'] = data.index.year
    data['Month'] = data.index.month
    data['Day'] = data.index.day

    close = data['Close'].shift(1)

    data['MA5'] = close.rolling(window=5).mean()
    data['MA10'] = close.rolling(window=10).mean()
    data['MA20'] = close.rolling(window=20).mean()

    delta = close.diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    RS = gain / loss
    RSI = 100 - (100 / (1 + RS))
    data.loc[data.index >= RSI.index[0], 'RSI'] = RSI

    exp1 = close.ewm(span=12, adjust=False).mean()
    exp2 = close.ewm(span=26, adjust=False).mean()
    MACD = exp1 - exp2
    data.loc[data.index >= MACD.index[0], 'MACD'] = MACD

    data['VWAP'] = (close * data['Volume']).cumsum() / data['Volume'].cumsum()

    period = 20
    data['SMA'] = close.rolling(window=period).mean()
    data['Std_dev'] = close.rolling(window=period).std()
    data['Upper_band'] = data['SMA'] + 2 * data['Std_dev']
    data['Lower_band'] = data['SMA'] - 2 * data['Std_dev']

    benchmark_data = yf.download('SPY', start=start_date, end=end_date)['Close']
    data['Relative_Performance'] = (close / benchmark_data.values) * 100

    data['ROC'] = (close.pct_change(periods=1)) * 100

    high_low_range = data['High'] - data['Low']
    high_close_range = abs(data['High'].shift(1) - close.shift(1))
    low_close_range = abs(data['Low'].shift(1) - close.shift(1))
    true_range = pd.concat([high_low_range, high_close_range, low_close_range], axis=1).max(axis=1)
    data['ATR'] = true_range.rolling(window=14).mean()

    data['Close_yes'] = data['Close'].shift(1)
    data['Open_yes'] = data['Open'].shift(1)
    data['High_yes'] = data['High'].shift(1)
    data['Low_yes'] = data['Low'].shift(1)

    data = data.dropna()
    return data

# 获取所有股票数据
stock_data = {ticker: get_stock_data(ticker) for ticker in tickers}
for ticker, data in stock_data.items():
    print(f"{ticker} data:\n{data.head()}\n")

def format_feature(data):
    features = ['Volume', 'Year', 'Month', 'Day', 'MA5', 'MA10', 'MA20', 'RSI', 'MACD', 
                'VWAP', 'SMA', 'Std_dev', 'Upper_band', 'Lower_band', 'Relative_Performance', 'ATR',
                'Close_yes', 'Open_yes', 'High_yes', 'Low_yes']
    X = data[features]
    y = data['Close'].pct_change()
    X = X.iloc[1:]
    y = y.iloc[1:]
    return X, y

# 格式化数据
stock_features = {ticker: format_feature(data) for ticker, data in stock_data.items()}
for ticker, (X, y) in stock_features.items():
    print(f"{ticker} features:\nX:\n{X.head()}\ny:\n{y.head()}\n")

# 进行参数调优的函数
def grid_search_lightgbm(X, y):
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # 定义LightGBM回归器
    estimator = lgb.LGBMRegressor()

    # 定义参数网格
    param_grid = {
        'num_leaves': [31, 50],
        'learning_rate': [0.05, 0.1, 0.2],
        'n_estimators': [100, 200],
        'subsample': [0.8, 1.0]
    }

    # 网格搜索
    gbm = GridSearchCV(estimator, param_grid, cv=5)
    gbm.fit(X_train, y_train)

    print(f"Best parameters found by grid search are: {gbm.best_params_}")
    print(f"Best score: {gbm.best_score_}")

    # 使用最佳参数训练模型
    best_model = gbm.best_estimator_
    best_model.fit(X_train, y_train)

    # 预测
    y_pred = best_model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    print(f"RMSE: {rmse}")

    return best_model

# 进行参数调优并训练模型
for ticker, (X, y) in stock_features.items():
    print(f"Training model for {ticker}")
    best_model = grid_search_lightgbm(X, y)


[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed


AAPL data:
                 Open       High        Low      Close  Adj Close     Volume  \
Date                                                                           
2020-01-31  80.232498  80.669998  77.072502  77.377502  75.086937  199588384   
2020-02-03  76.074997  78.372498  75.555000  77.165001  74.880722  173985604   
2020-02-04  78.827499  79.910004  78.408623  79.712502  77.352806  136616536   
2020-02-05  80.879997  81.190002  79.737503  80.362503  77.983574  118826872   
2020-02-06  80.642502  81.305000  80.066200  81.302498  78.895744  105425540   

            Year  Month  Day        MA5  ...   Std_dev  Upper_band  \
Date                                     ...                         
2020-01-31  2020      1   31  79.658000  ...  2.091398   82.191922   
2020-02-03  2020      2    3  79.218001  ...  1.982899   82.089422   
2020-02-04  2020      2    4  79.203500  ...  1.792484   81.848969   
2020-02-05  2020      2    5  79.261501  ...  1.638813   81.779752   
2020-02-